# 1st approach to Facial Emotion Recognition

In [1]:
import numpy as np
import cv2 as cv
import pandas as pd
import dlib
from imutils import face_utils
from sklearn.preprocessing import normalize
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.svm import LinearSVC
from sklearn.svm import SVC
from sklearn.preprocessing import StandardScaler
import xgboost as xgb
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from scipy.spatial.distance import pdist
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import matthews_corrcoef
from matplotlib import pyplot as plt
from torch import nn
import torch.nn.functional as F
from skorch import NeuralNetClassifier
import torch

## Preprocessing

First the dataset will be loaded.

In [2]:
x = [0]*980
y = [0]*980
from os import listdir
path = 'KDEF_and_AKDEF/KDEF'
folders = listdir(path)
c = 0
for f in folders:
    files = listdir(path + '/'+ f)
    for fi in files:
        if fi[6] == 'S':
            x[c] = cv.imread((path + '/' + f + '/' + fi))
            print(path + '/' + f + '/' + fi)
            y[c] = fi[4:6]
            c += 1

KDEF_and_AKDEF/KDEF/AF01/AF01AFS.JPG
KDEF_and_AKDEF/KDEF/AF01/AF01ANS.JPG
KDEF_and_AKDEF/KDEF/AF01/AF01DIS.JPG
KDEF_and_AKDEF/KDEF/AF01/AF01HAS.JPG
KDEF_and_AKDEF/KDEF/AF01/AF01NES.JPG
KDEF_and_AKDEF/KDEF/AF01/AF01SAS.JPG
KDEF_and_AKDEF/KDEF/AF01/AF01SUS.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02AFS.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02ANS.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02DIS.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02HAS.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02NES.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02SAS.JPG
KDEF_and_AKDEF/KDEF/AF02/AF02SUS.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03AFS.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03ANS.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03DIS.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03HAS.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03NES.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03SAS.JPG
KDEF_and_AKDEF/KDEF/AF03/AF03SUS.JPG
KDEF_and_AKDEF/KDEF/AF04/AF04AFS.JPG
KDEF_and_AKDEF/KDEF/AF04/AF04ANS.JPG
KDEF_and_AKDEF/KDEF/AF04/AF04DIS.JPG
KDEF_and_AKDEF/KDEF/AF04/AF04HAS.JPG
KDEF_and_AKDEF/KDEF/AF04/AF04NES.JPG
KDEF_and_AKDEF/KDEF/AF04/AF04SAS.JPG
K

KDEF_and_AKDEF/KDEF/AM29/AM29ANS.JPG
KDEF_and_AKDEF/KDEF/AM29/AM29DIS.JPG
KDEF_and_AKDEF/KDEF/AM29/AM29HAS.JPG
KDEF_and_AKDEF/KDEF/AM29/AM29NES.JPG
KDEF_and_AKDEF/KDEF/AM29/AM29SAS.JPG
KDEF_and_AKDEF/KDEF/AM29/AM29SUS.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30AFS.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30ANS.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30DIS.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30HAS.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30NES.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30SAS.JPG
KDEF_and_AKDEF/KDEF/AM30/AM30SUS.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31AFS.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31ANS.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31DIS.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31HAS.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31NES.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31SAS.JPG
KDEF_and_AKDEF/KDEF/AM31/AM31SUS.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32AFS.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32ANS.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32DIS.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32HAS.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32NES.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32SAS.JPG
KDEF_and_AKDEF/KDEF/AM32/AM32SUS.JPG
K

KDEF_and_AKDEF/KDEF/BM22/BM22DIS.JPG
KDEF_and_AKDEF/KDEF/BM22/BM22HAS.JPG
KDEF_and_AKDEF/KDEF/BM22/BM22NES.JPG
KDEF_and_AKDEF/KDEF/BM22/BM22SAS.JPG
KDEF_and_AKDEF/KDEF/BM22/BM22SUS.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23AFS.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23ANS.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23DIS.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23HAS.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23NES.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23SAS.JPG
KDEF_and_AKDEF/KDEF/BM23/BM23SUS.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24AFS.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24ANS.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24DIS.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24HAS.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24NES.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24SAS.JPG
KDEF_and_AKDEF/KDEF/BM24/BM24SUS.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25AFS.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25ANS.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25DIS.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25HAS.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25NES.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25SAS.JPG
KDEF_and_AKDEF/KDEF/BM25/BM25SUS.JPG
KDEF_and_AKDEF/KDEF/BM26/BM26AFS.JPG
K

In [3]:
len(x)

980

In [4]:
y

['AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',
 'HA',
 'NE',
 'SA',
 'SU',
 'AF',
 'AN',
 'DI',

In [5]:
y = np.array(y)
#y[y != 'NE']

Now 68 points on each face will be located.

In [6]:
# initialize dlib's face detector (HOG-based) and then create
# the facial landmark predictor
p = "shape_predictor_68_face_landmarks.dat"
detector = dlib.get_frontal_face_detector()
predictor = dlib.shape_predictor(p)

In [7]:
def preproc(x):
    desf = [0]*len(x)
    c = 0
    for image in x:
        
        # A 3x3 Gaussian Blur will now be applied
        image = cv.GaussianBlur(image, (3,3), 0)
        
        # Now need to apply a Contrast Adaptive Histogran Equalization
        image2 = cv.cvtColor(image, cv.COLOR_BGR2GRAY)
        clahe = cv.createCLAHE(clipLimit=4, tileGridSize=(8,8))
        cl1 = clahe.apply(image2.copy())
        
        # detect faces in the grayscale image
        rects = detector(cl1, 0)
        
        # loop over the face detections
        for (i, rect) in enumerate(rects):
            # determine the facial landmarks for the face region, then
            # convert the facial landmark (x, y)-coordinates to a NumPy
            # array
            shape = predictor(cl1, rect)
            shape = face_utils.shape_to_np(shape)
        
        # Calculate distances between the keypoints
        des = pdist(shape, 'euclidean')
        desf[c] = des
        c += 1
    return(desf)

In [8]:
desf = preproc(x)

In [9]:
desf = np.array(desf)
desf

array([[ 40.11234224,  80.75270893, 120.35364556, ...,  16.2788206 ,
         32.        ,  16.2788206 ],
       [ 43.18564576,  85.15867542, 129.06587465, ...,  14.14213562,
         30.01666204,  16.2788206 ],
       [ 38.11823711,  74.81310046, 113.4372073 , ...,  17.11724277,
         35.        ,  18.11077028],
       ...,
       [ 45.17742799,  88.68483523, 132.83448347, ...,  13.15294644,
         27.01851217,  14.03566885],
       [ 40.60788101,  77.46612163, 115.73245007, ...,  13.15294644,
         28.01785145,  15.03329638],
       [ 45.39823785,  88.45903006, 131.02671483, ...,  14.14213562,
         28.01785145,  14.03566885]])

In [10]:
X_train, X_test, y_train, y_test = train_test_split(desf, y, test_size=0.1, random_state=42)

In [11]:
len(X_train)

882

In [12]:
len(y_train)

882

Now y will be encoded

In [13]:
le = LabelEncoder()
le.fit(y_train)

LabelEncoder()

In [14]:
le.classes_

array(['AF', 'AN', 'DI', 'HA', 'NE', 'SA', 'SU'], dtype='<U2')

In [15]:
len(le.classes_)

7

In [16]:
y_actual = le.transform(y_train) 

X_train will now be normalized

In [17]:
scaler = StandardScaler().fit(X_train)

In [18]:
scaler

StandardScaler(copy=True, with_mean=True, with_std=True)

In [19]:
scaler.mean_

array([ 43.22777512,  85.58499952, 128.38492984, ...,  17.91603692,
        35.9293955 ,  18.35510712])

In [20]:
scaler.scale_

array([2.77685645, 5.40694631, 7.79522759, ..., 3.00335752, 5.88305065,
       3.0458361 ])

In [21]:
X_train = scaler.transform(X_train)

In [22]:
X_test = scaler.transform(X_test)

## SVM classifiers

In [24]:
clf = SVC(kernel='rbf')

params = {
    'gamma': ['scale', 'auto', 0.001, 0.01, 0.1, 1, 10, 100],
    'C': [0.001, 0.01, 0.1, 1]
}

gs = RandomizedSearchCV(clf, params, refit=False, cv=10, scoring='accuracy', verbose=3, random_state=42) #verbose=2

gs.fit(X_train, y_actual)
print(gs.best_score_, gs.best_params_)

Fitting 10 folds for each of 10 candidates, totalling 100 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.15384615384615385, total=   2.7s


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    4.3s remaining:    0.0s


[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.15384615384615385, total=   2.7s


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    8.8s remaining:    0.0s


[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.14444444444444443, total=   2.7s
[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.14444444444444443, total=   3.4s
[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.14606741573033707, total=   2.9s
[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.14772727272727273, total=   3.1s
[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.14942528735632185, total=   2.9s
[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.14942528735632185, total=   2.7s
[CV] gamma=1, C=1 ....................................................
[CV] .......... gamma=1, C=1, score=0.15294117647058825, total=   2.9s
[CV] g

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:  6.6min finished
C:\Users\Manvir\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:841: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)


0.7834467120181405 {'gamma': 'scale', 'C': 1}


In [25]:
clf = SVC(kernel='rbf', gamma='scale', C=1)
clf.fit(X_train, y_train)
pred = clf.predict(X_test)

In [26]:
confusion_matrix(y_test, pred, labels=le.classes_)

array([[ 8,  1,  0,  0,  2,  1,  3],
       [ 1,  9,  0,  0,  2,  0,  0],
       [ 1,  0, 17,  0,  0,  2,  1],
       [ 1,  0,  0,  7,  0,  0,  0],
       [ 0,  0,  0,  0, 11,  1,  0],
       [ 2,  0,  3,  0,  1,  8,  0],
       [ 1,  0,  0,  0,  0,  0, 15]], dtype=int64)

In [27]:
print(classification_report(y_test, pred))

              precision    recall  f1-score   support

          AF       0.57      0.53      0.55        15
          AN       0.90      0.75      0.82        12
          DI       0.85      0.81      0.83        21
          HA       1.00      0.88      0.93         8
          NE       0.69      0.92      0.79        12
          SA       0.67      0.57      0.62        14
          SU       0.79      0.94      0.86        16

   micro avg       0.77      0.77      0.77        98
   macro avg       0.78      0.77      0.77        98
weighted avg       0.77      0.77      0.76        98



In [28]:
matthews_corrcoef(y_test, pred)

0.7244966068733685

In [29]:
clf = SVC(kernel='poly')

params = {
    'gamma': ['scale', 'auto', 0.001, 0.01, 0.1, 1, 10, 100],
    'degree': [0, 1, 2, 3, 4, 5, 6],
    'C': [0.001, 0.01, 0.1, 1]
}

gs = RandomizedSearchCV(clf, params, refit=False, cv=10, scoring='accuracy', verbose=3, random_state=42) #verbose=2

gs.fit(X_train, y_actual)
print(gs.best_score_, gs.best_params_)

Fitting 10 folds for each of 10 candidates, totalling 100 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.15384615384615385, total=   2.7s


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    4.3s remaining:    0.0s


[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.15384615384615385, total=   2.6s


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    8.4s remaining:    0.0s


[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.14444444444444443, total=   2.6s
[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.14444444444444443, total=   2.7s
[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.14606741573033707, total=   2.6s
[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.14772727272727273, total=   2.6s
[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.14942528735632185, total=   2.6s
[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001, score=0.14942528735632185, total=   2.8s
[CV] gamma=auto, degree=1, C=0.001 ...................................
[CV]  gamma=auto, degree=1, C=0.001

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed:  5.5min finished
C:\Users\Manvir\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:841: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)


0.8027210884353742 {'gamma': 0.1, 'degree': 1, 'C': 0.01}


In [30]:
clf = SVC(kernel='poly', gamma=0.1, degree=1, C=0.01)
clf.fit(X_train, y_train)
pred = clf.predict(X_test)

In [31]:
confusion_matrix(y_test, pred, labels=le.classes_)

array([[ 8,  1,  1,  0,  2,  1,  2],
       [ 1,  9,  0,  0,  2,  0,  0],
       [ 2,  1, 17,  0,  0,  1,  0],
       [ 0,  0,  0,  8,  0,  0,  0],
       [ 0,  0,  0,  0, 11,  1,  0],
       [ 1,  0,  3,  0,  1,  9,  0],
       [ 3,  0,  0,  0,  0,  0, 13]], dtype=int64)

In [32]:
print(classification_report(y_test, pred))

              precision    recall  f1-score   support

          AF       0.53      0.53      0.53        15
          AN       0.82      0.75      0.78        12
          DI       0.81      0.81      0.81        21
          HA       1.00      1.00      1.00         8
          NE       0.69      0.92      0.79        12
          SA       0.75      0.64      0.69        14
          SU       0.87      0.81      0.84        16

   micro avg       0.77      0.77      0.77        98
   macro avg       0.78      0.78      0.78        98
weighted avg       0.77      0.77      0.76        98



In [33]:
matthews_corrcoef(y_test, pred)

0.7241422212233977

## Neural Networks

### One Hidden Layer

First the best hyperparameters for a neural network with one hidden layer will be determined.

In [23]:
H1 = int(((len(y)+len(le.classes_)))/2)
print('H1: ' + str(H1))
class MyModule(nn.Module):
    def __init__(self, dropout = 0.5, hl = len(desf[0])):
        super().__init__()
        self.module = nn.Sequential(
            nn.Linear(X_train.shape[1], hl),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(hl, len(le.classes_))
        )

    def forward(self, X):
        return self.module(X)

net = NeuralNetClassifier(
    MyModule,
    criterion = nn.CrossEntropyLoss,
    optimizer=torch.optim.Adam,
    max_epochs=10,
    lr=0.3,
    # Shuffle training data on each epoch
    #iterator_train__shuffle=True,
    #iterator_valid__shuffle=True,
)

params = {
    'lr': [0.00001, 0.00005, 0.0001, 0.0005, 0.001, 0.005, 0.01, 0.05, 0.1, 0.5, 1.0, 5.0],
    'max_epochs': [20, 40, 60, 80, 100, 120, 140, 160, 180, 200, 400, 600, 800, 1000],
    'optimizer__weight_decay': [0, 0.000001, 0.00001, 0.0001, 0.001, 0.01, 0.1],
    'module__dropout': [0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'module__hl': [7, 14, 20, 40, 60, 80, 100, 120, 140, 200, 300, 400, 500, 600, 700, 800, 900, 1000],
    #'optimizer__nesterov': [False, True]
}
gs = RandomizedSearchCV(net, params, refit=False, cv=10, scoring='accuracy', verbose=2, random_state=42)

gs.fit(X_train.astype(np.float32), y_actual.astype(np.int64))
print(gs.best_score_, gs.best_params_)

H1: 493
Fitting 10 folds for each of 10 candidates, totalling 100 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] optimizer__weight_decay=0.001, module__hl=900, module__dropout=0.7, max_epochs=800, lr=0.01 
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1       18.3727       0.5528       11.6827  0.1835
      2       14.6246       0.6646        7.4834  0.2042
      3       14.4198       0.7329        7.8670  0.1963
      4       13.4434       0.7205       11.3048  0.1973
      5       14.6291       0.7516        7.2531  0.1944
      6       16.0743       0.7329       10.6440  0.1987
      7       13.6172       0.7888        8.2391  0.2260
      8       15.0486       0.7453        9.9061  0.2042
      9       15.1232       0.7640       11.1130  0.1939
     10       14.9913       0.7888       10.5310  0.1902
     11       15.9455       0.7888       11.7695  0.1899
     12       16.4179       0.7640       12.0944  0.1999
     13       15.6142       0.7950       12.0884  0.2363
     14       16.9695       0.7826        9.084

    284       25.8820       0.8199       49.5496  0.1780
    285       24.8849       0.8385       53.1666  0.1767
    286       28.1870       0.8385       44.0475  0.1703
    287       30.0460       0.8137       54.3041  0.1739
    288       29.2380       0.8509       57.3640  0.1742
    289       27.0495       0.8447       52.6388  0.1822
    290       20.6603       0.8509       54.3068  0.1787
    291       21.0676       0.8509       62.6494  0.1789
    292       25.8151       0.8137       61.5345  0.1885
    293       20.1629       0.8261       62.8367  0.1834
    294       17.1919       0.8261       53.8448  0.1801
    295       21.0068       0.8323       47.3972  0.1741
    296       27.8606       0.7702       66.3544  0.1697
    297       30.5106       0.8199       50.5803  0.1724
    298       25.4019       0.8385       57.7871  0.1735
    299       24.8888       0.8696       47.5444  0.1795
    300       21.2714       0.8323       53.9862  0.1739
    301       23.9188       0.8

    570       21.8884       0.8385       54.1820  0.1801
    571       24.2028       0.8509       46.1167  0.1741
    572       22.1750       0.8323       48.2178  0.1816
    573       24.9966       0.8385       60.3554  0.1718
    574       29.9286       0.8696       62.4274  0.1806
    575       25.1047       0.8447       57.3001  0.1744
    576       35.7112       0.8447       52.8589  0.1687
    577       27.0682       0.8571       44.5123  0.1781
    578       22.8286       0.8758       51.9762  0.1722
    579       21.9821       0.8571       60.9838  0.1741
    580       19.8184       0.8012       68.0995  0.1680
    581       22.7651       0.8323       59.9973  0.1791
    582       29.7931       0.8323       56.6071  0.1729
    583       17.8864       0.8509       47.7701  0.1840
    584       24.0510       0.8696       64.3021  0.1698
    585       26.1726       0.8509       69.5856  0.1780
    586       18.6275       0.8696       68.4442  0.1840
    587       22.0458       0.8

...

     58     4158.0304       0.7950     4290.9987  0.0679
     59     4574.0983       0.8199     5187.5648  0.0639
     60     4268.5815       0.8075     6211.3228  0.0759
     61     4291.4613       0.8137     5005.5614  0.0759
     62     4539.5364       0.7888     4793.3129  0.0639
     63     4946.7087       0.7950     8856.1660  0.0639
     64     4325.2682       0.8012     7575.1176  0.0559
     65     6301.3801       0.7950     6755.4076  0.0599
     66     5479.0807       0.7950     6848.5163  0.0559
     67     4996.3217       0.8323     5454.9202  0.0639
     68     4049.3758       0.7888     9123.4037  0.0559
     69     4383.5019       0.7950     6739.9147  0.0599
     70     4540.9077       0.7950     6005.0240  0.0555
     71     4034.1337       0.8199     5818.9994  0.0559
     72     5054.5928       0.8199     7102.3492  0.0559
     73     4769.5401       0.8012     6327.6020  0.0639
     74     4798.8981       0.8012     6196.1694  0.0599
     75     3953.7329       0.7

     14     2366.2801       0.7485     1857.4314  0.0599
     15     2330.2984       0.7362     1867.6517  0.0599
     16     2231.1457       0.7914     1841.1275  0.0599
     17     2383.9089       0.7362     2008.1128  0.0653
     18     2579.9618       0.7423     2434.6124  0.0599
     19     2410.1987       0.7914     2327.8933  0.0572
     20     2779.9231       0.7853     1688.7569  0.0599
     21     2595.8276       0.7301     2229.6577  0.0639
     22     2637.0445       0.7975     2585.6011  0.0599
     23     2308.1462       0.7669     2026.7594  0.0599
     24     3515.1748       0.7791     2958.2214  0.0559
     25     2835.6131       0.7914     2217.7420  0.0599
     26     2364.9211       0.8037     1601.6329  0.0559
     27     2430.1060       0.7975     2371.5315  0.0639
     28     3242.4864       0.7669     2230.4381  0.0599
     29     2181.0578       0.7669     2795.8591  0.0679
     30     3210.3010       0.7239     3061.4548  0.0599
     31     3577.5311       0.7

    135     4758.7062       0.8160     8684.8447  0.0599
    136     6416.6450       0.7853    17011.4324  0.0599
    137     4768.8572       0.8160    10043.1597  0.0599
    138     4429.9321       0.8160    10466.5148  0.0559
    139     6187.2389       0.8098    12450.6209  0.0630
    140     5492.5580       0.8160    10667.2156  0.0572
    141     4145.2048       0.8037    13307.5266  0.0519
    142     4206.9961       0.7791    14109.6967  0.0519
    143     5912.9931       0.7914    14013.7691  0.0599
    144     5258.8952       0.8037    16129.8403  0.0556
    145     4886.6367       0.8037    10500.1257  0.0572
    146     6623.5826       0.8160    16637.3752  0.0719
    147     4703.3886       0.8160    11997.2746  0.0599
    148     4132.5371       0.8221    13639.6983  0.0559
    149     5373.9101       0.8282    13333.4007  0.0599
    150     4789.1255       0.8037    10573.0604  0.0559
    151     4034.8014       0.8282    12868.2381  0.0639
    152     5988.8281       0.8

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed: 110.3min finished
C:\Users\Manvir\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:841: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)


0.8140589569160998 {'optimizer__weight_decay': 0.001, 'module__hl': 1000, 'module__dropout': 0.9, 'max_epochs': 400, 'lr': 0.05}


Now test accuracy will be determined

In [25]:
H1 = int(((len(y)+len(le.classes_)))/2)
print('H1: ' + str(H1))
class MyModule(nn.Module):
    def __init__(self, dropout = 0.5, hl = len(desf[0])):
        super().__init__()
        self.module = nn.Sequential(
            nn.Linear(X_train.shape[1], hl),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(hl, len(le.classes_))
        )

    def forward(self, X):
        return self.module(X)

net = NeuralNetClassifier(
    MyModule,
    criterion = nn.CrossEntropyLoss,
    optimizer=torch.optim.Adam,
    optimizer__weight_decay=0.001,
    module__hl=1000,
    module__dropout=0.9,
    max_epochs=400,
    lr=0.05,
    # Shuffle training data on each epoch
    #iterator_train__shuffle=True,
    #iterator_valid__shuffle=True,
)

net.fit(X_train.astype(np.float32), y_actual.astype(np.int64))
pred = net.predict(X_test.astype(np.float32))
pred = le.inverse_transform(pred)

H1: 493
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1      346.5003       0.5754      287.8058  0.2250
      2      681.4738       0.6257      271.2187  0.2317
      3     1011.0450       0.7039      332.6974  0.2198
      4     1052.4112       0.7039      361.1684  0.2236
      5     1149.3507       0.7318      411.0607  0.2329
      6     1382.2180       0.7542      460.8896  0.2454
      7     1676.2685       0.7151      658.9275  0.2300
      8     1861.5254       0.6704      657.4526  0.2237
      9     1818.7819       0.7430      922.5821  0.2197
     10     2046.3855       0.7486      559.0984  0.2142
     11     2022.2263       0.7430      878.5826  0.2690
     12     2483.3766       0.7039      780.3166  0.2397
     13     2122.3045       0.7542      691.4933  0.2387
     14     2457.4856       0.7263      962.1884  0.2202
     15     1985.4487       0.7374      643.6666  0.2210
     16     2166.0262  

    285     2674.4521       0.8436     1438.6807  0.2277
    286     2536.4145       0.8492     1053.2982  0.2277
    287     2131.9107       0.8324     1097.7321  0.2157
    288     2587.8750       0.8324     1293.3789  0.2440
    289     2247.8184       0.8492     1275.9285  0.2369
    290     2645.3261       0.8436     1208.9106  0.2237
    291     2529.7183       0.8380     1402.1876  0.2197
    292     2378.1606       0.8492     1333.1291  0.2175
    293     2391.1384       0.8324     1284.9984  0.2226
    294     2503.5365       0.8380     1334.9447  0.2197
    295     2326.9670       0.8268     1182.1493  0.2157
    296     2652.5109       0.8324     1440.6449  0.2157
    297     2468.5341       0.8324     1637.2969  0.2157
    298     2772.3943       0.8436     1405.9619  0.2117
    299     2760.4446       0.8156     1388.0950  0.2087
    300     2305.8056       0.8268     1877.6530  0.2157
    301     2661.0862       0.8045     1554.2912  0.2277
    302     3017.1300       0.8

In [27]:
accuracy_score(y_test, pred)

0.7959183673469388

In [28]:
confusion_matrix(y_test, pred, labels=le.classes_)

array([[ 7,  2,  1,  0,  1,  0,  4],
       [ 1,  9,  0,  0,  1,  1,  0],
       [ 0,  2, 18,  0,  0,  0,  1],
       [ 0,  0,  0,  8,  0,  0,  0],
       [ 0,  0,  0,  0, 11,  1,  0],
       [ 1,  0,  3,  0,  0, 10,  0],
       [ 1,  0,  0,  0,  0,  0, 15]], dtype=int64)

In [29]:
print(classification_report(y_test, pred))

              precision    recall  f1-score   support

          AF       0.70      0.47      0.56        15
          AN       0.69      0.75      0.72        12
          DI       0.82      0.86      0.84        21
          HA       1.00      1.00      1.00         8
          NE       0.85      0.92      0.88        12
          SA       0.83      0.71      0.77        14
          SU       0.75      0.94      0.83        16

   micro avg       0.80      0.80      0.80        98
   macro avg       0.81      0.81      0.80        98
weighted avg       0.79      0.80      0.79        98



In [30]:
matthews_corrcoef(y_test, pred)

0.7611108419558006

### Two Hidden Layers

First the best hyperparameters for a neural network with two hidden layers will be determined.

In [24]:
class MyModule(nn.Module):
    def __init__(self, dropout = 0.5, hl = H1, h2 = H1):
        super().__init__()
        self.module = nn.Sequential(
            nn.Linear(X_train.shape[1], hl),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(hl, h2),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(h2, len(le.classes_))
        )

    def forward(self, X):
        return self.module(X)

net = NeuralNetClassifier(
    MyModule,
    criterion = nn.CrossEntropyLoss,
    optimizer=torch.optim.Adam,
    max_epochs=10,
    lr=0.3,
    # Shuffle training data on each epoch
    #iterator_train__shuffle=True,
    #iterator_valid__shuffle=True,
)

params = {
    'lr': [0.00001, 0.00005, 0.0001, 0.0005, 0.001, 0.005, 0.01, 0.05, 0.1, 0.5, 1.0, 5.0],
    'max_epochs': [20, 40, 60, 80, 100, 120, 140, 160, 180, 200, 400, 600, 800, 1000],
    'optimizer__weight_decay': [0, 0.000001, 0.00001, 0.0001, 0.001, 0.01, 0.1],
    'module__dropout': [0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9],
    'module__hl': [20, 40, 60, 80, 100, 120, 140, 200, 300, 400, 500, 600, 700, 800, 900, 1000],
    #'optimizer__nesterov': [False, True],
    'module__h2': [20, 40, 60, 80, 100, 120, 140, 200, 300, 400, 500, 600, 700, 800, 900, 1000]
}
gs = RandomizedSearchCV(net, params, refit=False, cv=10, scoring='accuracy', verbose=2, random_state=42)

gs.fit(X_train.astype(np.float32), y_actual.astype(np.int64))
print(gs.best_score_, gs.best_params_)

Fitting 10 folds for each of 10 candidates, totalling 100 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] optimizer__weight_decay=0.01, module__hl=200, module__h2=120, module__dropout=0.8, max_epochs=600, lr=0.1 
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1      445.4241       0.1118       38.4239  0.0851
      2      243.7841       0.1429        1.9585  0.0879
      3      102.9196       0.1429        1.9525  0.0995
      4       36.9926       0.1429        1.9466  0.0839
      5       42.1237       0.1491        1.9460  0.0879
      6       57.9950       0.1491        1.9470  0.0839
      7       18.3010       0.1491        1.9464  0.0759
      8       37.2020       0.1491        1.9458  0.0799
      9       32.8205       0.1429        1.9460  0.0879
     10       19.6160       0.1429        1.9462  0.0799
     11       29.4671       0.1429        1.9460  0.0759
     12       22.9572       0.1429        1.9458  0.0759
     13       27.4948       0.1429        1.9459  0.0879
     14       16.3352       0.149

    283        2.3830       0.1491        1.9458  0.0799
    284        3.1313       0.1491        1.9458  0.0854
    285        7.9837       0.1491        1.9457  0.0771
    286        4.1941       0.1429        1.9459  0.0799
    287       15.6505       0.1491        1.9459  0.0851
    288       43.5766       0.1491        1.9459  0.0919
    289        5.1486       0.1491        1.9458  0.0806
    290        3.6489       0.1491        1.9458  0.0719
    291        2.0524       0.1429        1.9459  0.0809
    292        1.9466       0.1429        1.9458  0.0799
    293        4.2029       0.1429        1.9459  0.0799
    294        7.0501       0.1429        1.9461  0.0799
    295        2.4091       0.1429        1.9460  0.0867
    296        5.5676       0.1491        1.9458  0.0771
    297       15.8973       0.1491        1.9457  0.0759
    298        3.2879       0.1491        1.9459  0.0759
    299       19.9973       0.1491        1.9458  0.0759
    300        8.3556       0.1

    569      107.4127       0.1491        1.9460  0.0879
    570        7.2896       0.1491        1.9460  0.1119
    571        1.9464       0.1491        1.9459  0.0999
    572        1.9466       0.1429        1.9458  0.0955
    573        1.9466       0.1491        1.9457  0.0839
    574        1.9466       0.1491        1.9457  0.0879
    575        1.9464       0.1491        1.9458  0.0839
    576        1.9464       0.1491        1.9458  0.0883
    577        1.9465       0.1491        1.9458  0.0879
    578        1.9465       0.1491        1.9458  0.0879
    579        1.9466       0.1491        1.9458  0.0959
    580       10.7616       0.1491        1.9458  0.0879
    581        3.7540       0.1491        1.9459  0.0839
    582        1.9646       0.1429        1.9458  0.0799
    583       58.5922       0.1429        1.9459  0.0879
    584       18.3928       0.1429        1.9460  0.0999
    585        2.4716       0.1491        1.9459  0.0839
    586        1.9464       0.1

...

    309        4.1796       0.1472        1.9455  0.1119
    310        1.9517       0.1472        1.9456  0.1039
    311       14.6223       0.1472        1.9456  0.1236
    312        4.9090       0.1472        1.9456  0.1227
    313        2.5477       0.1472        1.9456  0.1198
    314        2.7372       0.1472        1.9456  0.1119
    315        1.9461       0.1472        1.9456  0.1158
    316        2.9451       0.1472        1.9455  0.1368
    317        2.1916       0.1472        1.9455  0.1091
    318        4.0073       0.1472        1.9456  0.1198
    319        6.2966       0.1472        1.9456  0.1278
    320       10.3171       0.1472        1.9456  0.1131
    321        1.9400       0.1472        1.9456  0.1132
    322       11.5804       0.1472        1.9456  0.1131
    323        6.0027       0.1472        1.9456  0.1079
    324       37.0385       0.1472        1.9456  0.1119
    325        1.9431       0.1472        1.9456  0.1158
    326        1.9461       0.1

    595        1.9461       0.1472        1.9455  0.1267
    596        1.9461       0.1472        1.9455  0.1264
    597        5.4717       0.1472        1.9455  0.1318
    598        1.9461       0.1472        1.9455  0.1079
    599        1.9461       0.1472        1.9455  0.1079
    600        1.9461       0.1472        1.9456  0.1119
    601        2.7079       0.1472        1.9456  0.1198
    602       12.2864       0.1472        1.9456  0.1238
    603       10.8825       0.1472        1.9455  0.1318
    604       20.2508       0.1472        1.9455  0.1344
    605       10.7089       0.1472        1.9455  0.1293
    606        5.1858       0.1472        1.9456  0.1274
    607        1.9460       0.1472        1.9456  0.1198
    608        4.2626       0.1472        1.9456  0.1385
    609       13.2201       0.1472        1.9455  0.1119
    610        1.9461       0.1472        1.9455  0.1278
    611        2.0314       0.1472        1.9455  0.1214
    612        1.9461       0.1

    881        1.9461       0.1472        1.9455  0.1158
    882        9.9131       0.1472        1.9456  0.1291
    883        1.9461       0.1472        1.9455  0.1198
    884        1.9461       0.1472        1.9455  0.1212
    885        1.9430       0.1472        1.9455  0.1357
    886        1.9461       0.1472        1.9455  0.1238
    887        1.9461       0.1472        1.9456  0.1238
    888        1.9461       0.1472        1.9456  0.1198
    889        1.9698       0.1472        1.9456  0.1278
    890        1.9461       0.1472        1.9456  0.1212
    891        1.9461       0.1472        1.9456  0.1158
    892        1.9461       0.1472        1.9456  0.1957
    893        1.9461       0.1472        1.9456  0.1481
    894        1.9461       0.1472        1.9456  0.1185
    895        1.9461       0.1472        1.9456  0.1132
    896        1.9461       0.1472        1.9456  0.1158
    897        1.9431       0.1472        1.9456  0.1079
    898        1.9461       0.1

[Parallel(n_jobs=1)]: Done 100 out of 100 | elapsed: 173.9min finished
C:\Users\Manvir\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\model_selection\_search.py:841: DeprecationWarning: The default of the `iid` parameter will change from True to False in version 0.22 and will be removed in 0.24. This will change numeric results when test-set sizes are unequal.
  DeprecationWarning)


0.8321995464852607 {'optimizer__weight_decay': 1e-06, 'module__hl': 120, 'module__h2': 400, 'module__dropout': 0.8, 'max_epochs': 800, 'lr': 0.0001}


Now the test accuracy will be determined

In [24]:
H1 = 493

In [29]:
class MyModule(nn.Module):
    def __init__(self, dropout = 0.5, hl = H1, h2 = H1):
        super().__init__()
        self.module = nn.Sequential(
            nn.Linear(X_train.shape[1], hl),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(hl, h2),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(h2, len(le.classes_))
        )

    def forward(self, X):
        return self.module(X)

net = NeuralNetClassifier(
    MyModule,
    optimizer=torch.optim.Adam,
    optimizer__weight_decay=1e-06,
    module__hl=120,
    module__h2=400,
    module__dropout=0.8,
    max_epochs=800,
    lr=0.0001,
    # Shuffle training data on each epoch
    #iterator_train__shuffle=True,
    #iterator_valid__shuffle=True,
)

net.fit(X_train.astype(np.float32), y_actual.astype(np.int64))
pred = net.predict(X_test.astype(np.float32))
pred = le.inverse_transform(pred)

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1           nan       0.1508           nan  0.0759
      2           nan       0.1508           nan  0.0882
      3           nan       0.1508           nan  0.0839
      4           nan       0.1508           nan  0.0770
      5           nan       0.1508           nan  0.0840
      6           nan       0.1508           nan  0.0800
      7           nan       0.1508           nan  0.0800
      8           nan       0.1508           nan  0.0760
      9           nan       0.1508           nan  0.0800
     10           nan       0.1508           nan  0.0800
     11           nan       0.1508           nan  0.0800
     12           nan       0.1508           nan  0.0830
     13           nan       0.1508           nan  0.0761
     14           nan       0.1508           nan  0.0786
     15           nan       0.1508           nan  0.0780
     16           nan       0.1

In [32]:
accuracy_score(y_test, pred)

0.1326530612244898

In [33]:
confusion_matrix(y_test, pred, labels=le.classes_)

array([[ 1,  0,  0,  0, 14,  0,  0],
       [ 0,  0,  0,  0, 12,  0,  0],
       [ 0,  0,  0,  0, 21,  0,  0],
       [ 0,  0,  0,  0,  8,  0,  0],
       [ 0,  0,  0,  0, 12,  0,  0],
       [ 0,  0,  0,  0, 14,  0,  0],
       [ 2,  0,  0,  0, 14,  0,  0]], dtype=int64)

In [34]:
print(classification_report(y_test, pred))

C:\Users\Manvir\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\metrics\classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

          AF       0.33      0.07      0.11        15
          AN       0.00      0.00      0.00        12
          DI       0.00      0.00      0.00        21
          HA       0.00      0.00      0.00         8
          NE       0.13      1.00      0.22        12
          SA       0.00      0.00      0.00        14
          SU       0.00      0.00      0.00        16

   micro avg       0.13      0.13      0.13        98
   macro avg       0.07      0.15      0.05        98
weighted avg       0.07      0.13      0.04        98



In [35]:
matthews_corrcoef(y_test, pred)

0.04133333945601842